In [5]:
import pandas as pd
import numpy as np
import faiss

In [13]:
df = pd.read_csv('books.csv')
df

bookID                                              title  \
0           1  Harry Potter and the Half-Blood Prince (Harry ...   
1           2  Harry Potter and the Order of the Phoenix (Har...   
2           4  Harry Potter and the Chamber of Secrets (Harry...   
3           5  Harry Potter and the Prisoner of Azkaban (Harr...   
4           8  Harry Potter Boxed Set  Books 1-5 (Harry Potte...   
...       ...                                                ...   
11122   45631   Expelled from Eden: A William T. Vollmann Reader   
11123   45633                        You Bright and Risen Angels   
11124   45634                    The Ice-Shirt (Seven Dreams #1)   
11125   45639                                        Poor People   
11126   45641                        Las aventuras de Tom Sawyer   

                                                 authors average_rating  \
0                             J.K. Rowling/Mary GrandPré           4.57   
1                             J.K. Rowling/Mary GrandPré           4.49   
2                                           J.K. Rowling           4.42   
3                             J.K. Rowling/Mary GrandPré           4.56   
4                             J.K. Rowling/Mary GrandPré           4.78   
...                                                  ...            ...   
11122  William T. Vollmann/Larry McCaffery/Michael He...           4.06   
11123                                William T. Vollmann           4.08   
11124                                William T. Vollmann           3.96   
11125                                William T. Vollmann           3.72   
11126                                         Mark Twain           3.91   

             isbn       isbn13 language_code   num_pages  ratings_count  \
0       439785960  9.78044E+12           eng         652        2095690   
1       439358078  9.78044E+12           eng         870        2153167   
2       439554896  9.78044E+12           eng         352           6333   
3      043965548X  9.78044E+12           eng         435        2339585   
4       439682584  9.78044E+12           eng        2690          41428   
...           ...          ...           ...         ...            ...   
11122  1560254416  9.78156E+12           eng         512            156   
11123   140110879  9.78014E+12           eng         635            783   
11124   140131965  9.78014E+12           eng         415            820   
11125    60878827  9.78006E+12           eng         434            769   
11126  8497646983   9.7885E+12           spa         272            113   

       text_reviews_count publication_date        publisher Unnamed: 12  
0                   27591        9/16/2006  Scholastic Inc.         NaN  
1                   29221       09/01/2004  Scholastic Inc.         NaN  
2                     244       11/01/2003       Scholastic         NaN  
3                   36325       05/01/2004  Scholastic Inc.         NaN  
4                     164        9/13/2004       Scholastic         NaN  
...                   ...              ...              ...         ...  
11122                  20       12/21/2004    Da Capo Press         NaN  
11123                  56       12/01/1988    Penguin Books         NaN  
11124                  95       08/01/1993    Penguin Books         NaN  
11125                 139        2/27/2007             Ecco         NaN  
11126                  12        5/28/2006    Edimat Libros         NaN  

[11127 rows x 13 columns]

In [15]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11127 entries, 0 to 11126
Data columns (total 13 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   bookID              11127 non-null  int64 
 1   title               11127 non-null  object
 2   authors             11127 non-null  object
 3   average_rating      11127 non-null  object
 4   isbn                11127 non-null  object
 5   isbn13              11127 non-null  object
 6   language_code       11127 non-null  object
 7     num_pages         11127 non-null  object
 8   ratings_count       11127 non-null  int64 
 9   text_reviews_count  11127 non-null  int64 
 10  publication_date    11127 non-null  object
 11  publisher           11127 non-null  object
 12  Unnamed: 12         4 non-null      object
dtypes: int64(3), object(10)
memory usage: 1.1+ MB


In [16]:
df['embedding_text'] = df['title'].astype(str) + " by " + df['authors'].astype(str)

In [17]:
texts = df['embedding_text'].tolist()

In [18]:
texts

['Harry Potter and the Half-Blood Prince (Harry Potter  #6) by J.K. Rowling/Mary GrandPré',
 'Harry Potter and the Order of the Phoenix (Harry Potter  #5) by J.K. Rowling/Mary GrandPré',
 'Harry Potter and the Chamber of Secrets (Harry Potter  #2) by J.K. Rowling',
 'Harry Potter and the Prisoner of Azkaban (Harry Potter  #3) by J.K. Rowling/Mary GrandPré',
 'Harry Potter Boxed Set  Books 1-5 (Harry Potter  #1-5) by J.K. Rowling/Mary GrandPré',
 'Unauthorized Harry Potter Book Seven News: "Half-Blood Prince" Analysis and Speculation by W. Frederick Zimmerman',
 'Harry Potter Collection (Harry Potter  #1-6) by J.K. Rowling',
 "The Ultimate Hitchhiker's Guide: Five Complete Novels and One Story (Hitchhiker's Guide to the Galaxy  #1-5) by Douglas Adams",
 "The Ultimate Hitchhiker's Guide to the Galaxy (Hitchhiker's Guide to the Galaxy  #1-5) by Douglas Adams",
 "The Hitchhiker's Guide to the Galaxy (Hitchhiker's Guide to the Galaxy  #1) by Douglas Adams",
 "The Hitchhiker's Guide to the G

In [20]:
max = 700
overlap = 100
chunks = [] 
i = 0

In [21]:
while i < len(texts):
    piece = texts[i: i+max]
    chunks.append(piece)
    i = i + max - overlap
    

In [22]:
chunks

[['Harry Potter and the Half-Blood Prince (Harry Potter  #6) by J.K. Rowling/Mary GrandPré',
  'Harry Potter and the Order of the Phoenix (Harry Potter  #5) by J.K. Rowling/Mary GrandPré',
  'Harry Potter and the Chamber of Secrets (Harry Potter  #2) by J.K. Rowling',
  'Harry Potter and the Prisoner of Azkaban (Harry Potter  #3) by J.K. Rowling/Mary GrandPré',
  'Harry Potter Boxed Set  Books 1-5 (Harry Potter  #1-5) by J.K. Rowling/Mary GrandPré',
  'Unauthorized Harry Potter Book Seven News: "Half-Blood Prince" Analysis and Speculation by W. Frederick Zimmerman',
  'Harry Potter Collection (Harry Potter  #1-6) by J.K. Rowling',
  "The Ultimate Hitchhiker's Guide: Five Complete Novels and One Story (Hitchhiker's Guide to the Galaxy  #1-5) by Douglas Adams",
  "The Ultimate Hitchhiker's Guide to the Galaxy (Hitchhiker's Guide to the Galaxy  #1-5) by Douglas Adams",
  "The Hitchhiker's Guide to the Galaxy (Hitchhiker's Guide to the Galaxy  #1) by Douglas Adams",
  "The Hitchhiker's Gui

In [23]:
len(chunks)

19

In [35]:
pip install sentence-transformers


  Using cached sentence_transformers-5.1.0-py3-none-any.whl.metadata (16 kB)
  Using cached transformers-4.55.4-py3-none-any.whl.metadata (41 kB)
  Using cached huggingface_hub-0.34.4-py3-none-any.whl.metadata (14 kB)
  Using cached filelock-3.19.1-py3-none-any.whl.metadata (2.1 kB)
  Using cached tokenizers-0.21.4-cp39-abi3-win_amd64.whl.metadata (6.9 kB)
  Using cached safetensors-0.6.2-cp38-abi3-win_amd64.whl.metadata (4.1 kB)
  Using cached fsspec-2025.7.0-py3-none-any.whl.metadata (12 kB)
  Using cached sympy-1.14.0-py3-none-any.whl.metadata (12 kB)
  Using cached jinja2-3.1.6-py3-none-any.whl.metadata (2.9 kB)
  Using cached mpmath-1.3.0-py3-none-any.whl.metadata (8.6 kB)
  Using cached joblib-1.5.1-py3-none-any.whl.metadata (5.6 kB)
  Using cached threadpoolctl-3.6.0-py3-none-any.whl.metadata (13 kB)
Using cached sentence_transformers-5.1.0-py3-none-any.whl (483 kB)
Using cached transformers-4.55.4-py3-none-any.whl (11.3 MB)
Using cached huggingface_hub-0.34.4-py3-none-any.whl 

In [36]:
from sentence_transformers import SentenceTransformer

model = SentenceTransformer("Qwen/Qwen3-Embedding-0.6B")

def generate_embeddings(texts):
    return model.encode(texts, show_progress_bar=True)

text_emb = generate_embeddings(texts)

c:\Users\Datacell\anaconda3\envs\vectorDB\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Batches: 100%|██████████| 1/1 [00:17<00:00, 17.99s/it]


In [38]:
text_emb

array([[ 0.07402942,  0.05302087, -0.00724671, ...,  0.01038561,
         0.04488303, -0.02349464],
       [-0.00123636,  0.03558341, -0.00639273, ...,  0.00704351,
        -0.01006004,  0.00951987],
       [ 0.03971398, -0.00371272, -0.00919863, ...,  0.02661253,
        -0.00903542,  0.0005584 ],
       ...,
       [-0.01524599,  0.01099179, -0.01354709, ...,  0.00784391,
        -0.00070778, -0.06323031],
       [ 0.09789769, -0.03426601, -0.01219438, ..., -0.0009281 ,
         0.04569918,  0.00966911],
       [ 0.00535139,  0.03105958, -0.00563598, ...,  0.0101702 ,
        -0.01181495, -0.02418973]], shape=(19, 1024), dtype=float32)

In [ ]:
vectorList = []
meta = []

In [74]:
for idx, chunk in enumerate(chunks):
    vectorList.append(text_emb.astype("float32"))
    meta.append({"chunk": idx, "index": idx})

In [76]:
vectorList

[array([[ 0.07402942,  0.05302087, -0.00724671, ...,  0.01038561,
          0.04488303, -0.02349464],
        [-0.00123636,  0.03558341, -0.00639273, ...,  0.00704351,
         -0.01006004,  0.00951987],
        [ 0.03971398, -0.00371272, -0.00919863, ...,  0.02661253,
         -0.00903542,  0.0005584 ],
        ...,
        [-0.01524599,  0.01099179, -0.01354709, ...,  0.00784391,
         -0.00070778, -0.06323031],
        [ 0.09789769, -0.03426601, -0.01219438, ..., -0.0009281 ,
          0.04569918,  0.00966911],
        [ 0.00535139,  0.03105958, -0.00563598, ...,  0.0101702 ,
         -0.01181495, -0.02418973]], shape=(19, 1024), dtype=float32),
 array([[ 0.07402942,  0.05302087, -0.00724671, ...,  0.01038561,
          0.04488303, -0.02349464],
        [-0.00123636,  0.03558341, -0.00639273, ...,  0.00704351,
         -0.01006004,  0.00951987],
        [ 0.03971398, -0.00371272, -0.00919863, ...,  0.02661253,
         -0.00903542,  0.0005584 ],
        ...,
        [-0.01524599,

In [77]:
meta

[{'chunk': ['Harry Potter and the Half-Blood Prince (Harry Potter  #6) by J.K. Rowling/Mary GrandPré',
   'Harry Potter and the Order of the Phoenix (Harry Potter  #5) by J.K. Rowling/Mary GrandPré',
   'Harry Potter and the Chamber of Secrets (Harry Potter  #2) by J.K. Rowling',
   'Harry Potter and the Prisoner of Azkaban (Harry Potter  #3) by J.K. Rowling/Mary GrandPré',
   'Harry Potter Boxed Set  Books 1-5 (Harry Potter  #1-5) by J.K. Rowling/Mary GrandPré',
   'Unauthorized Harry Potter Book Seven News: "Half-Blood Prince" Analysis and Speculation by W. Frederick Zimmerman',
   'Harry Potter Collection (Harry Potter  #1-6) by J.K. Rowling',
   "The Ultimate Hitchhiker's Guide: Five Complete Novels and One Story (Hitchhiker's Guide to the Galaxy  #1-5) by Douglas Adams",
   "The Ultimate Hitchhiker's Guide to the Galaxy (Hitchhiker's Guide to the Galaxy  #1-5) by Douglas Adams",
   "The Hitchhiker's Guide to the Galaxy (Hitchhiker's Guide to the Galaxy  #1) by Douglas Adams",
   "

In [50]:
type(vectorList)

list

In [89]:
data = np.vstack(vectorList).astype("float32")
data

array([[ 0.07402942,  0.05302087, -0.00724671, ...,  0.01038561,
         0.04488303, -0.02349464],
       [-0.00123636,  0.03558341, -0.00639273, ...,  0.00704351,
        -0.01006004,  0.00951987],
       [ 0.03971398, -0.00371272, -0.00919863, ...,  0.02661253,
        -0.00903542,  0.0005584 ],
       ...,
       [-0.01524599,  0.01099179, -0.01354709, ...,  0.00784391,
        -0.00070778, -0.06323031],
       [ 0.09789769, -0.03426601, -0.01219438, ..., -0.0009281 ,
         0.04569918,  0.00966911],
       [ 0.00535139,  0.03105958, -0.00563598, ...,  0.0101702 ,
        -0.01181495, -0.02418973]], shape=(2888, 1024), dtype=float32)

In [90]:
data

array([[ 0.07402942,  0.05302087, -0.00724671, ...,  0.01038561,
         0.04488303, -0.02349464],
       [-0.00123636,  0.03558341, -0.00639273, ...,  0.00704351,
        -0.01006004,  0.00951987],
       [ 0.03971398, -0.00371272, -0.00919863, ...,  0.02661253,
        -0.00903542,  0.0005584 ],
       ...,
       [-0.01524599,  0.01099179, -0.01354709, ...,  0.00784391,
        -0.00070778, -0.06323031],
       [ 0.09789769, -0.03426601, -0.01219438, ..., -0.0009281 ,
         0.04569918,  0.00966911],
       [ 0.00535139,  0.03105958, -0.00563598, ...,  0.0101702 ,
        -0.01181495, -0.02418973]], shape=(2888, 1024), dtype=float32)

In [91]:
faiss.normalize_L2(data)

In [92]:
data

array([[ 0.07402943,  0.05302088, -0.00724671, ...,  0.01038561,
         0.04488303, -0.02349464],
       [-0.00123636,  0.03558341, -0.00639273, ...,  0.00704351,
        -0.01006004,  0.00951987],
       [ 0.03971398, -0.00371272, -0.00919863, ...,  0.02661254,
        -0.00903543,  0.0005584 ],
       ...,
       [-0.01524599,  0.01099179, -0.01354709, ...,  0.00784391,
        -0.00070778, -0.06323031],
       [ 0.09789769, -0.03426601, -0.01219438, ..., -0.0009281 ,
         0.04569918,  0.00966911],
       [ 0.00535139,  0.03105957, -0.00563598, ...,  0.0101702 ,
        -0.01181495, -0.02418972]], shape=(2888, 1024), dtype=float32)

In [93]:
d = data.shape[1]

In [94]:
d

1024

In [95]:
index = faiss.IndexFlatIP(d)

In [96]:
index.add(data)

In [97]:
import json

indexFile = "book_index.faiss"
metaFile = "book_meta.json"

In [98]:
faiss.write_index(index, indexFile)

In [99]:
with open (metaFile, 'w') as f:
    json.dump(meta, f)

In [100]:
def recommedation(query, k=5):
    query_ = generate_embeddings(query)
    query_vector = query_.astype("float32").reshape(1, -1)
    faiss.normalize_L2(query_vector)
    D, I = index.search(query_vector, k)

    print(f"Top {k} recommendation for {query}:\n")
    for idx in I[0]:
        book = df.iloc[idx]
        print(f"Title: {book['title']}, Author: {book['authors']} (Rating: {book['average_rating']})")
    

In [103]:
recommedation("A book about magic")

Batches: 100%|██████████| 1/1 [00:18<00:00, 18.31s/it]


Top 5 recommendation for A book about magic:

Title: Power of an Hour: Business and Life Mastery in One Hour a Week, Author: Dave Lakhani (Rating: 3.34)
Title: Always Enough: God's Miraculous Provision Among the Poorest Children on Earth, Author: Heidi Baker/Rolland Baker (Rating: 4.46)
Title: The Changeling (Daughters of England  #15), Author: Philippa Carr (Rating: 3.98)
Title: Notes from a Small Island, Author: Bill Bryson (Rating: 3.91)
Title: Harry Potter and the Half-Blood Prince (Harry Potter  #6), Author: J.K. Rowling/Mary GrandPré (Rating: 4.57)
